topo prepare and rainfall data prepare

In [ ]:
import numpy as np
from PIL import Image
from matplotlib.colors import LinearSegmentedColormap
import matplotlib.pyplot as plt
# Custom colormap
color_values_normalized = np.array([
    [64, 64, 103], [64, 64, 179], [64, 255, 178], [89, 255, 64], [157, 255, 64],
    [211, 255, 64], [255, 254, 64], [255, 213, 64], [255, 176, 64], [255, 141, 64],
    [255, 109, 64], [255, 78, 64], [255, 78, 78], [255, 106, 106], [255, 133, 133],
    [255, 159, 159], [255, 184, 184], [255, 208, 208], [255, 231, 231], [255, 254, 254]
]) / 255.0
custom_cmap = LinearSegmentedColormap.from_list("custom_cmap", color_values_normalized)

# Load image
img_path = 'topo.png'
img = Image.open(img_path)
img_array = np.array(img)

# We need to convert the image array to a format that corresponds to the elevation values.
# Since the color_values_normalized correspond to specific elevation values, we need a function
# that maps each pixel's color to the closest color in the custom_cmap and then to the elevation value.

# This function will find the closest color in the colormap for a given pixel
def find_closest_color(pixel, colormap):
    # Calculate the difference between the pixel and colormap colors in RGB space
    deltas = np.sum((colormap - pixel) ** 2, axis=1)
    # Find the index of the closest color
    index = np.argmin(deltas)
    return index

# Map the image to the new colormap by finding the closest color for each pixel
mapped_indices = np.zeros((img_array.shape[0], img_array.shape[1]), dtype=int)

for i in range(img_array.shape[0]):
    for j in range(img_array.shape[1]):
        mapped_indices[i, j] = find_closest_color(img_array[i, j] / 255.0, color_values_normalized)

# Now we need to map these indices to the elevation values
elevation_values = np.array([-81, -54, 8, 98, 212, 349, 506, 684, 881, 1096, 1329, 1579, 1846, 2129, 2429, 2744, 3074, 3420, 3780, 4155])
mapped_elevation = elevation_values[mapped_indices]

# Let's save the array to a file so it can be downloaded
np.save('mapped_elevation.npy', mapped_elevation)

mapped_elevation_file_path = 'mapped_elevation.npy'


In [ ]:
# We will now load the numpy array from the file and display it as an image using the custom colormap.

# Load the numpy array from the saved file
mapped_elevation = np.load('mapped_elevation.npy')

# Use the custom colormap for display
plt.imshow(mapped_elevation, cmap=custom_cmap)
plt.colorbar(label='Elevation')
plt.title('Elevation Map')
plt.show()
print("Shape of the array:", mapped_elevation.shape)

In [ ]:
from netCDF4 import Dataset
import numpy as np

# Replace with your actual file path
file_path = 'adaptor.mars.internal-1700975833.6327882-23227-8-68fdc913-4e87-4c39-a755-4ae92a9e6fed.nc'

# Open the NetCDF file
nc_file = Dataset(file_path, 'r')

# Assuming you know the variable name you want to extract, for example 'temperature'
variable_name = 'tp'
data = np.array(nc_file.variables[variable_name][:])

# Close the file
nc_file.close()

# Optionally, save the numpy array to a .npy file
np.save('my_data.npy', data)

print("Shape of the array:", data.shape)
print("Data type of the elements:", data.dtype)
print("Total number of elements:", data.size)
print("Size of each element (in bytes):", data.itemsize)
print("Total size of the array (in bytes):", data.nbytes)

In [ ]:
# Calculate the mean over the first dimension (axis=0)
mean_data = np.mean(data, axis=0)

# Check the shape of the resulting array
mean_tp = mean_data.shape
print("Shape of the array:", mean_tp)
plt.imshow(mean_data)
plt.colorbar(label='Elevation')
plt.title('Elevation Map')
plt.show()

average = np.mean(data)
average

erosion part

In [ ]:
%matplotlib qt 
# On Macs use osx
# For Windows use qt

import numpy as np
from numpy.random import rand
from landscapeWithOcean import LandscapeWithOcean # Import methods from inside file landscapeWithOcean.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
import matplotlib.animation as animation

In [ ]:
import numpy as np
import scipy.ndimage

# 调整重新采样比率以确保输出尺寸为200x200
adjusted_resampled_array = scipy.ndimage.zoom(mapped_elevation, (200/761, 200/730), order=3, mode='nearest')

# 再次应用高斯滤波器进行平滑处理
adjusted_smoothed_array = scipy.ndimage.gaussian_filter(adjusted_resampled_array, sigma=1)

adjusted_resampled_array.shape, adjusted_smoothed_array.shape  # 显示调整后重新采样和平滑处理后的数组尺寸





In [ ]:
# 定义Z为调整大小并平滑处理后的数组
Z = adjusted_smoothed_array

# 沿Y方向反转Z
Z_flipped = np.flip(Z, axis=0)

Z = Z_flipped


In [ ]:
NX = 201
NY = 195
x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x) #strange that y goes first !!!
# Z = adjusted_smoothed_array
ZMaxOrg = np.max(Z)
#print(ZMaxOrg)

fig = plt.figure()
ax = fig.add_subplot(121, projection='3d')
ax.plot_surface(X, Y, Z, cmap='viridis')
ax.set_title("3D Image")

ax2 = fig.add_subplot(122)
c = ax2.imshow(Z, origin='lower', cmap='viridis')
plt.colorbar(c, ax=ax2)
ax2.set_title("2D Image")

plt.tight_layout()
plt.show()

In [ ]:
### Physical Parameters
K = average/100 # meters^(1-2m)/yr    

D = 0.01 # m^2/yr

# uplift rate
# uplift = 0.03 / 600.
uplift = 0.00003

In [ ]:
d = 1300
#dt = d**2 / D / 8. 
#dt = d**2 / D /16. #extra small steps 
dt = 0.1
print(' dt[years] = ',dt)

#Area exponent A^m, default m=1
m=1

#gradient exponent g^n, default n=1
n=1

#erosion threshold 
theta_c = 10 

In [ ]:
# Total simulation time
T = 1000.0 * dt

# total number of iterations
n_iter = int(np.round(T/dt))
print('Number of interation: ',n_iter)

In [ ]:
# Initialize landscape 
ls = LandscapeWithOcean(NX,NY)

oceanLevelParameter=0.03  # what does this parameter do?  # the parameter is used to locate the sea level and beach level. the get the range of the ocean
ls.ComputeOceanVolumeFromOceanLevelParameter(Z,NX,NY,oceanLevelParameter)

ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

In [ ]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

def update_figure():
        plt.clf()
        ax1 = fig.add_subplot(121,projection='3d')

        # use equal x-y aspect with an explicit vertical exageration
        vert_exag = 4.
        ax1.set_xlim3d(0,max(NX,NY))
        ax1.set_ylim3d(0,max(NX,NY))
        ax1.set_zlim3d(0,ZMaxOrg)

        ax1.set_title('Surface Relief')

#        surf = ax1.plot_surface(X,Y,Z, cmap = cm.terrain, rstride=1, cstride=1,
#                antialiased=False,linewidth=0)

        ZPlot = np.copy(Z)
        ZPlot[ZPlot<ls.ZBeachLevel] = ls.ZBeachLevel 
        ZPlot -= ls.ZBeachLevel
        ax1.plot_surface(X,Y,ZPlot, cmap = cm.terrain, rstride=1, cstride=1,
                antialiased=False,linewidth=0)

        ax2 = fig.add_subplot(122,aspect='equal')
        ax2.set_title('Elevation')

        #im = ax2.pcolor(Z,cmap=cm.terrain)
        im = ax2.pcolor(ZPlot,cmap=cm.coolwarm)
        cs = ax2.contour(ZPlot,6,colors='k')

        # Add a color bar which maps values to colors.
        cbar = fig.colorbar(im, shrink=0.5, aspect=5)
        # Add the contour line levels to the colorbar
        cbar.add_lines(cs)

        #plt.show()
        plt.draw()
#         plt.pause(0.0001)
#         writer.grab_frame()

In [ ]:
# Set up figure
fig = init_figure()
update_figure()
Znew = np.copy(Z)
dx = d # keep dx=dy for simplicity
dy = d
def animate(it):
    global Z, NX, NY, Znew
    ls.calculate_collection_area(Z,NX,NY)

#     for it in range(1,n_iter+1):
    
    ls.calculate_collection_area(Z,NX,NY)
    ls.A *= dx*dy
    
    for i in range(NX):
        iL = np.mod(i-1,NX) # normally i-1 but observe p.b.c.
        iR = np.mod(i+1,NX) # normally i+1 but observe p.b.c.

        for j in range(NY):
            jD = np.mod(j-1,NY) # normally j-1 but observe p.b.c.
            jU = np.mod(j+1,NY) # normally j+1 but observe p.b.c.
  
            if ls.ocean[i,j]>0:
                Psi_z  = 0;
                Phi_z  = 0;
            else:
                if ls.drain[i,j]>0: #this cell is a drain
                    s1 = (Z[iR,j]  - Z[iL,j] )/(2.*dx)
                    s2 = (Z[i,jU]  - Z[i,jD] )/(2.*dy)
                    s3 = (Z[iR,jD] - Z[iL,jU])/(2. * np.sqrt( dx**2 + dy**2) )
                    s4 = (Z[iR,jU] - Z[iL,jD])/(2. * np.sqrt( dx**2 + dy**2) )
                    gradient = (np.sqrt(s1**2 + s2**2) + np.sqrt(s3**2 + s4**2))/2.
                    Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)            

                elif ls.drainage[i,j]>0: #this cell is a drainage point (it drains a pool)
                
                    if (Z[i,j]>=Z[iR,j]) and ls.pool[iR,j]!=ls.drainage[i,j]: 
                        gradient = (Z[i,j]-Z[iR,j])/dx #pool is on my left, I drain to the right, use this gradiant
                    elif (Z[i,j]>=Z[iL,j]) and ls.pool[iL,j]!=ls.drainage[i,j]:
                        gradient = (Z[i,j]-Z[iL,j])/dx
                    elif (Z[i,j]>=Z[i,jU]) and ls.pool[i,jU]!=ls.drainage[i,j]:
                        gradient = (Z[i,j]-Z[i,jU])/dy
                    elif (Z[i,j]>=Z[i,jD]) and ls.pool[i,jD]!=ls.drainage[i,j]:
                        gradient = (Z[i,j]-Z[i,jD])/dy
                    else:
                        gradient = 0.02 # ??? This does happen (maybe when two pools merge)
                    Psi_z = K * ( ls.A[i,j]**m * gradient**n - theta_c)
                
                else: #this cell is a pool, assume it has some mass diffusion but no erosion!
                    Psi_z = 0.
                
                if (Psi_z<0):
                    Psi_z = 0. 

                # diffusion term
                Phi_z = D * ( (Z[iR,j] - 2.*Z[i,j] + Z[iL,j]) / dx**2 \
                            + (Z[i,jU] - 2.*Z[i,j] + Z[i,jD]) / dx**2 )
           
            Znew[i,j] = Z[i,j] + (Phi_z - Psi_z + uplift )*dt  

            dZdt= (Znew[i,j] - Z[i,j]) / dt
            CFL = abs(dZdt) * dt / min(dx,dy)
            if (CFL>1.0):
                print('\nWarning: Time step of',dt,'is probably too large. Safer would be:',dt/CFL)
            
            if (Znew[i,j]<0.):
                Znew[i,j] = 0. # yes, this does happen at the boundary when kept at zero
    
        #Znew[0,:] = 0.0 # resets front boundary to 0
    Z = np.copy(Znew)
    
    ls.pool_check(Z,NX,NY)

    if (np.mod(it,10)==0): 
        print(it,end='')
        update_figure()
        print(' Ocean level=',ls.ZBeachLevel,' Ocean surface fraction=',100*ls.AOcean/(NX*NY));
    else:
        print('.',end='')

update_figure()
#     print(' Simulation finished.')
ani = animation.FuncAnimation(fig, animate, frames=n_iter, repeat=False)

# 保存为.mp4文件
ani.save('result200200.mp4', writer='ffmpeg', fps=120) #你可以调整fps根据你的需求

print(' Simulation finished.')